In [1]:
import requests
import os
import time
import numpy as np 
import pandas as pd
import matplotlib.pyplot as plt
from tqdm import tqdm

# "coin list" download

In [ ]:
def get_coin_list(isactive:bool):
    url = 'https://pro-api.coinmarketcap.com/v1/cryptocurrency/map'

    headers = {
    'Accepts': 'application/json',
    'X-CMC_PRO_API_KEY': 'e0070978-f2c5-4a31-b9b8-7705d84077bd',
    }

    isActive = 'active' if isactive else 'inactive'
    params = {
        'listing_status': isActive,
    }

    res = requests.get(url=url, headers=headers, params=params)

    return res

In [ ]:
# active랑 inactive를 가져옴
active = get_coin_list(isactive=True)
inactive = get_coin_list(isactive=False)

In [ ]:
active_data = active.json()["data"]
inactive_data = inactive.json()["data"]

In [ ]:
df_active = pd.DataFrame(active_data)
df_inactive = pd.DataFrame(inactive_data)
df_active.head()

In [ ]:
df_inactive.head()

In [ ]:
col = ["id","name","symbol","slug","is_active","first_historical_data","last_historical_data"]
df = pd.concat([df_active[col],df_inactive[col]]) \
       .dropna(thresh=6) \
       .reset_index(drop=True) # first_historical_data가 NaN인 친구들은 drop 

In [ ]:
df.to_csv("coin_list_coinmarketcap.csv")

# OHLCV Download

In [2]:
coin_list = pd.read_csv("coin_list_coinmarketcap.csv", index_col=0)
coin_list.head()

id       name symbol       slug  is_active     first_historical_data   
0   1    Bitcoin    BTC    bitcoin          1  2010-07-13T00:00:00.000Z  \
1   2   Litecoin    LTC   litecoin          1  2013-04-28T18:47:22.000Z   
2   3   Namecoin    NMC   namecoin          1  2013-04-28T18:47:22.000Z   
3   4  Terracoin    TRC  terracoin          1  2013-04-28T18:47:22.000Z   
4   5   Peercoin    PPC   peercoin          1  2013-04-28T18:47:23.000Z   

       last_historical_data  
0  2023-04-15T12:59:00.000Z  
1  2023-04-15T12:59:00.000Z  
2  2023-04-15T12:59:00.000Z  
3  2023-04-15T12:59:00.000Z  
4  2023-04-15T12:59:00.000Z

In [3]:
query_id = str(list(coin_list.id.values.tolist()))[1:-1].replace(" ","")
query_id

'1,2,3,4,5,6,8,10,13,16,18,25,35,42,43,45,52,53,56,61,64,66,67,69,72,74,77,78,80,83,87,90,93,99,109,118,120,122,128,131,132,141,145,148,154,162,168,170,182,184,201,213,215,217,254,258,260,263,268,276,278,290,291,293,298,313,316,328,333,360,362,366,367,372,377,389,405,416,448,460,463,470,501,502,506,512,541,551,558,572,576,584,588,597,601,624,638,644,656,659,693,702,703,707,720,730,733,760,764,788,789,799,815,819,825,831,833,837,853,857,859,873,894,895,898,911,916,918,921,934,938,945,948,951,978,986,993,1004,1019,1020,1026,1027,1032,1033,1035,1037,1038,1042,1044,1052,1053,1066,1070,1082,1085,1087,1090,1104,1106,1107,1120,1135,1136,1146,1154,1155,1156,1159,1164,1165,1168,1169,1172,1175,1185,1191,1194,1200,1209,1210,1212,1214,1216,1218,1223,1229,1230,1238,1241,1244,1247,1248,1250,1252,1254,1257,1259,1273,1274,1279,1281,1282,1285,1291,1294,1297,1298,1299,1306,1312,1320,1321,1340,1343,1351,1353,1368,1376,1382,1389,1392,1395,1396,1414,1437,1439,1447,1455,1466,1468,1473,1474,1492,1495,1500,15

In [4]:
numbers_list = list(map(int, query_id.split(",")))

# Initialize an empty list to store the groups
groups = []

# Iterate over the list of numbers and split them into groups of five
for i in range(0, len(numbers_list), 5):
    group = numbers_list[i:i+5]
    groups.append(group)

# Convert each group into a string and join them with commas
groups_strings = [",".join(map(str, group)) for group in groups]

In [5]:
def get_coin_ohlcv(group_string):
    url = 'https://pro-api.coinmarketcap.com/v2/cryptocurrency/ohlcv/historical'

    headers = {
    'Accepts': 'application/json',
    'X-CMC_PRO_API_KEY': 'e0070978-f2c5-4a31-b9b8-7705d84077bd',
    }

    params = {
        "id" : group_string,
        "time_period" : "daily", # hourly 가능...
        "time_start" : "2013-04-27", # coinmarketcap 데이터는 4월 28일부터 다운로드 된다   
        "time_end":"2018-04-17",
        "count":10000
        }

    res = requests.get(url=url, headers=headers, params=params)
    return res

In [6]:
len(groups_strings)
# 500개씩 나눠서 보내자

2165

In [15]:
return_dict = {}

for string in tqdm(groups_strings[500:]):
    s = string.split(",")[0]
    time.sleep(0.38)
    return_dict["g" + str(s)] = get_coin_ohlcv(string)

100%|██████████| 1665/1665 [52:45<00:00,  1.90s/it] 


In [16]:
return_dict#["g1"].json()#.text

{'g8635': <Response [200]>,
 'g8644': <Response [200]>,
 'g8653': <Response [200]>,
 'g8660': <Response [200]>,
 'g8670': <Response [200]>,
 'g8679': <Response [200]>,
 'g8691': <Response [200]>,
 'g8702': <Response [200]>,
 'g8709': <Response [200]>,
 'g8717': <Response [200]>,
 'g8726': <Response [200]>,
 'g8738': <Response [200]>,
 'g8752': <Response [200]>,
 'g8760': <Response [200]>,
 'g8771': <Response [200]>,
 'g8790': <Response [200]>,
 'g8800': <Response [200]>,
 'g8826': <Response [200]>,
 'g8835': <Response [200]>,
 'g8849': <Response [200]>,
 'g8863': <Response [200]>,
 'g8871': <Response [200]>,
 'g8880': <Response [200]>,
 'g8886': <Response [200]>,
 'g8899': <Response [200]>,
 'g8909': <Response [200]>,
 'g8916': <Response [200]>,
 'g8936': <Response [200]>,
 'g8942': <Response [200]>,
 'g8963': <Response [200]>,
 'g8971': <Response [200]>,
 'g8992': <Response [200]>,
 'g9002': <Response [200]>,
 'g9018': <Response [200]>,
 'g9024': <Response [200]>,
 'g9033': <Response 

In [17]:
final_list = []
error_key = {}

for key, values in tqdm(return_dict.items()):
    try:
        data = values.json()["data"]
        final_dict = {}
        
        for id, json in data.items():
            df = pd.DataFrame(json["quotes"])
            df_time = df.iloc[:,0:4]

            quote = df.quote
            open = quote.apply(lambda x: x["USD"]["open"])
            open.name = "open"
            close = quote.apply(lambda x: x["USD"]["close"])
            close.name = "close"
            low = quote.apply(lambda x: x["USD"]["low"])
            low.name = "low"
            high = quote.apply(lambda x: x["USD"]["high"])
            high.name = "high"
            vol = quote.apply(lambda x: x["USD"]["volume"])
            vol.name = "vol"
            mktcap = quote.apply(lambda x: x["USD"]["market_cap"])
            mktcap.name = "mktcap"

            concat_df = pd.concat([df_time, open,close, low, high,vol,mktcap], axis=1)
            final_dict[id] = concat_df
    except:
        error_key[id] = json
        print("Error Raised!!")
        
    final_list.append(final_dict)

100%|██████████| 1665/1665 [00:07<00:00, 229.70it/s]  


In [18]:
len(final_list)

1665

In [19]:
# Open, close, low, high, vol, mktcap, time 각각 따로 저장하자
df_close = pd.DataFrame()
df_low = pd.DataFrame()
df_high = pd.DataFrame()
df_vol = pd.DataFrame()
df_mktcap = pd.DataFrame()
df_open = pd.DataFrame()

df_time_high = pd.DataFrame()
df_time_low = pd.DataFrame()

for data_dict in tqdm(final_list):
    for coin_key, df in data_dict.items():
        df.index = pd.to_datetime(df.time_open).dt.strftime('%Y-%m-%d')
        df.index = pd.to_datetime(df.index)
        
        df_open[coin_key] = df.open
        df_close[coin_key] = df.close
        df_low[coin_key] = df.low
        df_high[coin_key] = df.high
        df_vol[coin_key] = df.vol
        df_mktcap[coin_key] = df.mktcap
        
        df_time_high[coin_key] = df.time_high
        df_time_low[coin_key] = df.time_low

 81%|████████  | 1341/1665 [00:00<00:00, 8834.30it/s]C:\Users\user\AppData\Local\Temp\ipykernel_10512\3902909006.py:17: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_open[coin_key] = df.open
C:\Users\user\AppData\Local\Temp\ipykernel_10512\3902909006.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_close[coin_key] = df.close
C:\Users\user\AppData\Local\Temp\ipykernel_10512\3902909006.py:19: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has po

In [20]:
df_close

7        12  15        17        19        20  22  23  24   
time_open                                                                      
2013-04-29  0.000374       NaN NaN       NaN       NaN       NaN NaN NaN NaN  \
2013-04-30  0.000341       NaN NaN       NaN       NaN       NaN NaN NaN NaN   
2013-05-01  0.000284       NaN NaN       NaN       NaN       NaN NaN NaN NaN   
2013-05-02  0.000255       NaN NaN       NaN       NaN       NaN NaN NaN NaN   
2013-05-03  0.000235       NaN NaN       NaN       NaN       NaN NaN NaN NaN   
...              ...       ...  ..       ...       ...       ...  ..  ..  ..   
2017-11-18  0.000013  0.000420 NaN  0.001170       NaN  0.075907 NaN NaN NaN   
2017-11-20  0.000015  0.000412 NaN  0.001071  0.104746  0.105228 NaN NaN NaN   
2017-11-21  0.000013  0.000471 NaN  0.000890  0.103285  0.064722 NaN NaN NaN   
2017-11-22  0.000020  0.000448 NaN  0.001316  0.105680  0.080922 NaN NaN NaN   
2017-11-23  0.000023  0.000458 NaN  0.001207       NaN  0.070227 NaN NaN NaN   

            26  ...  2532  2534  2550  2560  2574  2587  2590  2637  2639   
time_open       ...                                                         
2013-04-29 NaN  ...   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  \
2013-04-30 NaN  ...   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   
2013-05-01 NaN  ...   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   
2013-05-02 NaN  ...   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   
2013-05-03 NaN  ...   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   
...         ..  ...   ...   ...   ...   ...   ...   ...   ...   ...   ...   
2017-11-18 NaN  ...   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   
2017-11-20 NaN  ...   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   
2017-11-21 NaN  ...   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   
2017-11-22 NaN  ...   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   
2017-11-23 NaN  ...   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   

            2640  
time_open         
2013-04-29   NaN  
2013-04-30   NaN  
2013-05-01   NaN  
2013-05-02   NaN  
2013-05-03   NaN  
...          ...  
2017-11-18   NaN  
2017-11-20   NaN  
2017-11-21   NaN  
2017-11-22   NaN  
2017-11-23   NaN  

[1567 rows x 1487 columns]

In [21]:
# Save
df_close.to_pickle("df_close2.pickle")
df_low.to_pickle("df_low2.pickle")
df_high.to_pickle("df_high2.pickle")
df_vol.to_pickle("df_vol2.pickle")
df_mktcap.to_pickle("df_mktcap2.pickle")
df_open.to_pickle("df_open2.pickle")

df_time_high.to_pickle("df_time_high2.pickle")
df_time_low.to_pickle("df_time_low2.pickle")

## Data Concat

In [22]:
d1, d2 = {},{}
#d0,d1,d2,d3 = {},{},{},{}
i = 1

for dict in [d1,d2]:
    for path in os.listdir(f"sample/{str(i)}"):
        read = pd.read_pickle(f"sample/{str(i)}/{path}")
        read.index = pd.to_datetime(read.index)
        dict[path[:-7]] = read
    i += 1

In [23]:
#print(d0.keys())
print(d1.keys())
print(d2.keys())
#print(d3.keys())

dict_keys(['df_close1', 'df_high1', 'df_low1', 'df_mktcap1', 'df_open1', 'df_time_high1', 'df_time_low1', 'df_vol1'])
dict_keys(['df_close2', 'df_high2', 'df_low2', 'df_mktcap2', 'df_open2', 'df_time_high2', 'df_time_low2', 'df_vol2'])


In [34]:
d2["df_close2"].index

DatetimeIndex(['2013-04-29', '2013-04-30', '2013-05-01', '2013-05-02',
               '2013-05-03', '2013-05-04', '2013-05-05', '2013-05-06',
               '2013-05-07', '2013-05-08',
               ...
               '2017-11-13', '2017-11-14', '2017-11-15', '2017-11-16',
               '2017-11-17', '2017-11-18', '2017-11-20', '2017-11-21',
               '2017-11-22', '2017-11-23'],
              dtype='datetime64[ns]', name='time_open', length=1567, freq=None)

In [33]:
d1["df_close1"].index

DatetimeIndex(['2013-04-28', '2013-04-29', '2013-04-30', '2013-05-01',
               '2013-05-02', '2013-05-03', '2013-05-04', '2013-05-05',
               '2013-05-06', '2013-05-07',
               ...
               '2018-04-08', '2018-04-09', '2018-04-10', '2018-04-11',
               '2018-04-12', '2018-04-13', '2018-04-14', '2018-04-15',
               '2018-04-16', '2018-04-17'],
              dtype='datetime64[ns]', name='time_open', length=1816, freq=None)

In [35]:
new_dict = {}
for key in d1.keys():
    real_key = key[:-1]
    c1 = d1[real_key+str(1)]
    c2 = d2[real_key+str(2)]
    new_dict[real_key] = pd.concat([c1,c2], axis=1)

In [37]:
new_dict.keys()#["df_close"]

dict_keys(['df_close', 'df_high', 'df_low', 'df_mktcap', 'df_open', 'df_time_high', 'df_time_low', 'df_vol'])

# Data Concat 2013~2018 and 2018~2023

In [42]:
# 2013-2018을 담고 있음
new_dict.keys()

dict_keys(['df_close', 'df_high', 'df_low', 'df_mktcap', 'df_open', 'df_time_high', 'df_time_low', 'df_vol'])

In [52]:
# 2018-2023 데이터 불러오기
path = "coinmarketcap_data/2018~2023/"
old_dict = {}

for file in os.listdir(path):
    key_name = "df_" + str(file)[14:-7]
    old_dict[key_name] = pd.read_pickle(f"{path}{file}")    

In [53]:
old_dict.keys()

dict_keys(['df_close', 'df_high', 'df_low', 'df_mktcap', 'df_open', 'df_time_high', 'df_time_low', 'df_vol'])

In [54]:
# 두 데이터합치기
final_concat = {}

for key in old_dict.keys():
    past = new_dict[key]
    recent = old_dict[key]
    final_concat[key] = pd.concat([past, recent])

In [61]:
final_concat.keys()

dict_keys(['df_close', 'df_high', 'df_low', 'df_mktcap', 'df_open', 'df_time_high', 'df_time_low', 'df_vol'])

In [65]:
final_concat["df_open"][["1"]].isna().sum()

1    0
dtype: int64

In [ ]:
# 저장
final_concat["df_close"].to_pickle("coinmktcap_close.pickle")
final_concat["df_low"].to_pickle("coinmktcap_low.pickle")
final_concat["df_high"].to_pickle("coinmktcap_high.pickle")
final_concat["df_vol"].to_pickle("coinmktcap_vol.pickle")
final_concat["df_mktcap"].to_pickle("coinmktcap_mktcap.pickle")
final_concat["df_open"].to_pickle("coinmktcap_open.pickle")

final_concat["df_time_high"].to_pickle("coinmktcap_timehigh.pickle")
final_concat["df_time_low"].to_pickle("coinmktcap_timelow.pickle")

# Data Check

데이터 잘 들어왔는지 확인해보자

In [8]:
path = "coinmarketcap_data/2018~2023/"
data_dict = {}

for file in os.listdir(path):
    key_name = str(file)[14:-7]
    data_dict[key_name] = pd.read_pickle(f"{path}{file}")    

In [24]:
data_dict["close"]

1           2         3         4         5         6   
time_open                                                                      
2018-04-18   8163.419922  139.996994  1.706000  0.162639  2.009380  3.699600  \
2018-04-19   8294.309570  146.300003  1.804120  0.159794  2.154000  3.794560   
2018-04-20   8845.830078  155.537003  1.966470  0.163890  2.589130  4.149070   
2018-04-21   8895.580078  148.934006  1.844100  0.169367  2.404220  4.054720   
2018-04-22   8802.459961  146.774002  1.858350  0.154385  2.453560  4.102980   
...                  ...         ...       ...       ...       ...       ...   
2023-04-12  29892.988700   92.136437  1.520779  0.011936  0.465610  0.031991   
2023-04-13  30399.066385   94.259499  1.463622  0.012069  0.478798  0.039521   
2023-04-14  30485.700029   96.451976  1.468830  0.011517  0.487722  0.053651   
2023-04-15  30318.496953   96.868210  1.464349  0.011166  0.502939  0.052166   
2023-04-16  30315.355456  100.267446  1.466899  0.011771  0.475116  0.066704   

                   8        10        13        16  ...  10206  10216  10523   
time_open                                           ...                        
2018-04-18  0.235454  0.007424  0.139277  0.012373  ...    NaN    NaN    NaN  \
2018-04-19  0.243442  0.007520  0.147413  0.012642  ...    NaN    NaN    NaN   
2018-04-20  0.254141  0.008043  0.136190  0.013496  ...    NaN    NaN    NaN   
2018-04-21  0.251284  0.008125  0.151564  0.013393  ...    NaN    NaN    NaN   
2018-04-22  0.248610  0.008007  0.144319  0.013151  ...    NaN    NaN    NaN   
...              ...       ...       ...       ...  ...    ...    ...    ...   
2023-04-12  0.003944  0.001495  0.030646  0.037819  ...    NaN    NaN    NaN   
2023-04-13  0.003826  0.001520  0.031161  0.036638  ...    NaN    NaN    NaN   
2023-04-14  0.003661  0.003048  0.036580  0.040837  ...    NaN    NaN    NaN   
2023-04-15  0.003651  0.003033  0.033514  0.040034  ...    NaN    NaN    NaN   
2023-04-16  0.003638  0.000606  0.033503  0.034918  ...    NaN    NaN    NaN   

            10835  10957  11091  12555  14804  14935  15198  
time_open                                                    
2018-04-18    NaN    NaN    NaN    NaN    NaN    NaN    NaN  
2018-04-19    NaN    NaN    NaN    NaN    NaN    NaN    NaN  
2018-04-20    NaN    NaN    NaN    NaN    NaN    NaN    NaN  
2018-04-21    NaN    NaN    NaN    NaN    NaN    NaN    NaN  
2018-04-22    NaN    NaN    NaN    NaN    NaN    NaN    NaN  
...           ...    ...    ...    ...    ...    ...    ...  
2023-04-12    NaN    NaN    NaN    NaN    NaN    NaN    NaN  
2023-04-13    NaN    NaN    NaN    NaN    NaN    NaN    NaN  
2023-04-14    NaN    NaN    NaN    NaN    NaN    NaN    NaN  
2023-04-15    NaN    NaN    NaN    NaN    NaN    NaN    NaN  
2023-04-16    NaN    NaN    NaN    NaN    NaN    NaN    NaN  

[1825 rows x 9800 columns]

In [11]:
coin_list

id                      name           symbol             slug   
0          1                   Bitcoin              BTC          bitcoin  \
1          2                  Litecoin              LTC         litecoin   
2          3                  Namecoin              NMC         namecoin   
3          4                 Terracoin              TRC        terracoin   
4          5                  Peercoin              PPC         peercoin   
...      ...                       ...              ...              ...   
10817  11091               Mamasan Inu          MAMASAN      mamasan-inu   
10818  12555                Kalata USD             KUSD       kalata-usd   
10819  14804           Baby Trader Joe             BJOE  baby-trader-joe   
10820  14935            RING Financial             RING   ring-financial   
10821  15198  [Deprecated]Swipe (BEP2)  [Deprecated]SXP       swipe-bep2   

       is_active     first_historical_data      last_historical_data  
0              1  2010-07-13T00:00:00.000Z  2023-04-15T12:59:00.000Z  
1              1  2013-04-28T18:47:22.000Z  2023-04-15T12:59:00.000Z  
2              1  2013-04-28T18:47:22.000Z  2023-04-15T12:59:00.000Z  
3              1  2013-04-28T18:47:22.000Z  2023-04-15T12:59:00.000Z  
4              1  2013-04-28T18:47:23.000Z  2023-04-15T12:59:00.000Z  
...          ...                       ...                       ...  
10817          0  2021-07-29T10:48:10.000Z  2021-07-30T12:33:22.000Z  
10818          0  2021-10-14T13:27:04.000Z  2021-11-16T03:37:05.000Z  
10819          0  2021-11-19T03:36:06.000Z  2022-01-29T17:36:00.000Z  
10820          0  2021-11-22T04:00:07.000Z  2022-03-06T05:10:00.000Z  
10821          0  2021-11-26T03:15:27.000Z  2022-03-02T02:25:00.000Z  

[10822 rows x 7 columns]